In [89]:
import cv2
import mediapipe as mp
import numpy as np
from mediapipe.python.solutions import pose as mp_pose
import csv
import pandas as pd

In [90]:
drawing_utils = mp.solutions.drawing_utils
drawing_styles = mp.solutions.drawing_styles
pose = mp_pose.Pose()

I0000 00:00:1743663831.950939  480107 gl_context.cc:369] GL version: 2.1 (2.1 Metal - 89.3), renderer: Apple M4 Pro


W0000 00:00:1743663832.014108  967464 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743663832.022085  967464 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.


In [65]:
def pose_speed_angle_calculator(mediapipe_model, mediapipe_based_filter):
    cap = cv2.VideoCapture(0)
    mid_shoulder_list = []
    mid_heel_list = []
    speed_list = []
    angle_list = []
    try:
        with mediapipe_model as model:
            while cap.isOpened():
                success, image = cap.read()

                if not success:
                    print("Ignoring empty camera frame.")
                    continue     # If loading a video, use 'break' instead of 'continue'.

                # Flip the image horizontally for a later selfie-view display, and convert
                # the BGR image to RGB.
                image = cv2.cvtColor(cv2.flip(image, 1), cv2.COLOR_BGR2RGB)

                try:
                    results = model.process(image)
                except Exception:
                    results = None

                image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)

                if results and results.pose_landmarks:
                    result_image = mediapipe_based_filter(image, results)
                else:
                    result_image = image

                cv2.imshow('MediaPipe', result_image)
                if results.pose_landmarks:
                    right_shoulder = results.pose_landmarks.landmark[12]
                    left_shoulder = results.pose_landmarks.landmark[11]
                    mid_shoulder_list.append(((right_shoulder.x + left_shoulder.x)/2, (right_shoulder.y + left_shoulder.y)/2, (right_shoulder.z + left_shoulder.z)/2))
                    right_heel = results.pose_landmarks.landmark[30]
                    left_heel = results.pose_landmarks.landmark[29]
                    mid_heel_list.append(((right_heel.x + left_heel.x)/2, (right_heel.y + left_heel.y)/2, (right_heel.z + left_heel.z)/2))

                if len(mid_shoulder_list) > 1:
                    (x1, y1, z1) = mid_shoulder_list[-2]
                    (x2, y2, z2) = mid_shoulder_list[-1]
                    speed = np.sqrt((x2 - x1) ** 2 + (y2 - y1) ** 2 + (z2 - z1) ** 2) * 2
                    speed_list.append(speed)
                    print(speed_list)

                if len(mid_shoulder_list) > 1 and len(mid_heel_list) >1:
                    (xs, ys, zs) = mid_shoulder_list[-1]
                    (xh, yh, zh) = mid_heel_list[-1]
                    angle = np.degrees(np.arctan((yh - ys)/(xh - xs)))
                    angle_list.append(angle)
                    print(angle_list)

                if cv2.waitKey(5) & 0xFF == ord('q'):
                    break
                    
    finally:
        cap.release()
        cv2.destroyAllWindows()

    csv_filename = "fall_down_data.csv"
    with open(csv_filename, mode="w", newline="") as file:
        writer = csv.writer(file)
        writer.writerow(["Speed", "Angle"])
        writer.writerows(zip(speed_list, angle_list))
    return image, results


In [91]:
# see https://google.github.io/mediapipe/solutions/holistic#python-solution-api
Holistic = mp.solutions.holistic.Holistic

def draw_holistic_results(image, results, show_hands=False, show_face=False, show_pose=True):
    if show_hands:
        drawing_utils.draw_landmarks(
            image,
            results.left_hand_landmarks,
            mp.solutions.holistic.HAND_CONNECTIONS,
            connection_drawing_spec=drawing_styles.get_default_hand_connections_style()
        )

        drawing_utils.draw_landmarks(
            image,
            results.right_hand_landmarks,
            mp.solutions.holistic.HAND_CONNECTIONS,
            connection_drawing_spec=drawing_styles.get_default_hand_connections_style()
        )

    if show_face:
        drawing_utils.draw_landmarks(
            image,
            results.face_landmarks,
            mp.solutions.holistic.FACEMESH_CONTOURS,
            landmark_drawing_spec=drawing_utils.DrawingSpec(thickness=0, circle_radius=0, color=(255, 255, 255)),
            connection_drawing_spec=drawing_styles.get_default_face_mesh_contours_style()
        )

    if show_pose:
        drawing_utils.draw_landmarks(
            image,
            results.pose_landmarks,
            mp.solutions.holistic.POSE_CONNECTIONS,
            landmark_drawing_spec=drawing_styles.get_default_pose_landmarks_style()
        )
    
    return image

In [ ]:
last_image, last_results = pose_speed_angle_calculator(
    mediapipe_model=Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5),
    mediapipe_based_filter=draw_holistic_results
)

I0000 00:00:1743594822.440779  480107 gl_context.cc:369] GL version: 2.1 (2.1 Metal - 89.3), renderer: Apple M4 Pro
W0000 00:00:1743594822.498906  652081 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743594822.508447  652085 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743594822.509428  652087 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743594822.509584  652086 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743594822.509584  652088 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling supp

[0.21588880199760754]
[88.64690280203172]
[0.21588880199760754, 0.053043799012863185]
[88.64690280203172, 89.0940180156982]
[0.21588880199760754, 0.053043799012863185, 0.3394169654388732]
[88.64690280203172, 89.0940180156982, 89.2919781601864]
[0.21588880199760754, 0.053043799012863185, 0.3394169654388732, 0.14969073487816062]
[88.64690280203172, 89.0940180156982, 89.2919781601864, 89.60199035259316]


2025-04-02 13:53:43.250 python[9684:480107] _TIPropertyValueIsValid called with 16 on nil context!
2025-04-02 13:53:43.250 python[9684:480107] imkxpc_getApplicationProperty:reply: called with incorrect property value 16, bailing.
2025-04-02 13:53:43.250 python[9684:480107] Text input context does not respond to _valueForTIProperty:


[0.21588880199760754, 0.053043799012863185, 0.3394169654388732, 0.14969073487816062, 0.011931743691950958]
[88.64690280203172, 89.0940180156982, 89.2919781601864, 89.60199035259316, 89.842190523015]
[0.21588880199760754, 0.053043799012863185, 0.3394169654388732, 0.14969073487816062, 0.011931743691950958, 0.13116960028557334]
[88.64690280203172, 89.0940180156982, 89.2919781601864, 89.60199035259316, 89.842190523015, -89.88881982855067]
[0.21588880199760754, 0.053043799012863185, 0.3394169654388732, 0.14969073487816062, 0.011931743691950958, 0.13116960028557334, 0.1908839869164538]
[88.64690280203172, 89.0940180156982, 89.2919781601864, 89.60199035259316, 89.842190523015, -89.88881982855067, -89.97636571330595]
[0.21588880199760754, 0.053043799012863185, 0.3394169654388732, 0.14969073487816062, 0.011931743691950958, 0.13116960028557334, 0.1908839869164538, 0.10319449886137198]
[88.64690280203172, 89.0940180156982, 89.2919781601864, 89.60199035259316, 89.842190523015, -89.88881982855067, 

In [ ]:
def fall_detector(df, col1 = "Speed", col2 = "Angle"):
    """
    Custom fall detection classifier based on speed and angle.
    - speed: Speed of the person 
    - angle: Standing angle with respect to vertical (degrees)
    """
    fall_detected = False
    possible_fall = False
    min_index = 0
    for index in range(min_index, len(df)):
        if possible_fall:
            if 0 < abs(df.loc[index, col2]) < 10:
                print(f"Fall Confirmed at row {index}")
                fall_detected = True
                break  # Stop checking when fall is confirmed
            if abs(df.loc[index +1, col2]) > abs(df.loc[index, col2]):
                possible_fall = False
        if abs(df.loc[index, col1]) > 0.1 and abs(df.loc[index, col2]) < 45: # Fast movement and highly inclined
            possible_fall = True
            min_index = index
    if not fall_detected:
        print("No confirmed fall detected in the dataset.")
    return fall_detected

In [70]:
# Read CSV line by line
csv_file = 'fall_down_data.csv'
df = pd.read_csv(csv_file)
fall_detector(df)

Fall Confirmed at row 84


True

In [ ]:
def run_fall_detector(mediapipe_model, mediapipe_based_filter):
    cap = cv2.VideoCapture(0)
    mid_shoulder_list = []
    mid_heel_list = []
    speed_list = []
    angle_list = []
    try:
        with mediapipe_model as model:
            while cap.isOpened():
                success, image = cap.read()

                if not success:
                    print("Ignoring empty camera frame.")
                    continue     # If loading a video, use 'break' instead of 'continue'.

                # Flip the image horizontally for a later selfie-view display, and convert
                # the BGR image to RGB.
                image = cv2.cvtColor(cv2.flip(image, 1), cv2.COLOR_BGR2RGB)
                
                try:
                    results = model.process(image)
                except Exception:
                    results = None

                image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)

                if results and results.pose_landmarks:
                    result_image = mediapipe_based_filter(image, results)
                else:
                    result_image = image

                cv2.imshow('MediaPipe', result_image)
                if results.pose_landmarks:
                    right_shoulder = results.pose_landmarks.landmark[12]
                    left_shoulder = results.pose_landmarks.landmark[11]
                    mid_shoulder_list.append(((right_shoulder.x + left_shoulder.x)/2, (right_shoulder.y + left_shoulder.y)/2, (right_shoulder.z + left_shoulder.z)/2))
                    right_heel = results.pose_landmarks.landmark[30]
                    left_heel = results.pose_landmarks.landmark[29]
                    mid_heel_list.append(((right_heel.x + left_heel.x)/2, (right_heel.y + left_heel.y)/2, (right_heel.z + left_heel.z)/2))

                if len(mid_shoulder_list) > 1:
                    (x1, y1, z1) = mid_shoulder_list[-2]
                    (x2, y2, z2) = mid_shoulder_list[-1]
                    speed = np.sqrt((x2 - x1) ** 2 + (y2 - y1) ** 2 + (z2 - z1) ** 2) * 2
                    speed_list.append(speed)

                if len(mid_shoulder_list) > 1 and len(mid_heel_list) >1:
                    (xs, ys, zs) = mid_shoulder_list[-1]
                    (xh, yh, zh) = mid_heel_list[-1]
                    angle = np.degrees(np.arctan((yh - ys)/(xh - xs)))
                    angle_list.append(angle)

                fall_detected = False
                possible_fall = False
                min_index = 0
                if len(speed_list) > 1 and len(angle_list) > 1:
                    for index in range(min_index, len(angle_list)):
                        if possible_fall:
                            if 0 < abs(angle_list[index]) < 10:
                                print(f"Fall Confirmed.")
                                fall_detected = True
                                result_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
                                break  # Stop checking when fall is confirmed
                            if abs(angle_list[index]) > abs(angle_list[index -1]):
                                possible_fall = False
                        if abs(speed_list[index]) > 0.1 and abs(angle_list[index]) < 45: # Fast movement and highly inclined
                            possible_fall = True
                            min_index = index
                if not fall_detected:
                    print("No confirmed fall detected in the dataset.")
                    


                if cv2.waitKey(5) & 0xFF == ord('q'):
                    break
                    
    finally:
        cap.release()
        cv2.destroyAllWindows()

    return image, results


In [93]:
last_image, last_results = run_fall_detector(
    mediapipe_model=Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5),
    mediapipe_based_filter=draw_holistic_results
)

I0000 00:00:1743663856.545739  480107 gl_context.cc:369] GL version: 2.1 (2.1 Metal - 89.3), renderer: Apple M4 Pro
W0000 00:00:1743663856.604669  967829 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743663856.613166  967829 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743663856.615146  967836 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743663856.615253  967835 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1743663856.615590  967833 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling supp

No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirmed fall detected in the dataset.
No confirme